In [1]:
from __future__ import print_function

from keras.models import Sequential, Model
from keras.layers.embeddings import Embedding
from keras.layers import Input, Activation, Dense, Permute, Dropout, add, dot,merge, concatenate
from keras.layers import LSTM
from keras.utils.data_utils import get_file
from keras.preprocessing.sequence import pad_sequences
from functools import reduce
import tarfile
import numpy as np
import re

/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


In [2]:
def tokenize(sent):
    '''Return the tokens of a sentence including punctuation.
    >>> tokenize('Bob dropped the apple. Where is the apple?')
    ['Bob', 'dropped', 'the', 'apple', '.', 'Where', 'is', 'the', 'apple', '?']
    '''
    return [x.strip() for x in re.split('(\W+)?', sent) if x.strip()]



In [3]:
def parse_stories(lines, only_supporting=False):
    '''Parse stories provided in the bAbi tasks format
    If only_supporting is true, only the sentences
    that support the answer are kept.
    '''
    data = []
    story = []
    for line in lines:
        line = line.decode('utf-8').strip()
        nid, line = line.split(' ', 1)
        nid = int(nid)
        if nid == 1:
            story = []
        if '\t' in line:
            q, a, supporting = line.split('\t')
            q = tokenize(q)
            substory = None
            if only_supporting:
                # Only select the related substory
                supporting = map(int, supporting.split())
                substory = [story[i - 1] for i in supporting]
            else:
                # Provide all the substories
                substory = [x for x in story if x]
            data.append((substory, q, a))
            story.append('')
        else:
            sent = tokenize(line)
            story.append(sent)
        #print(data)
    return data


In [4]:
def get_stories(f, only_supporting=False, max_length=None):
    '''Given a file name, read the file,
    retrieve the stories,
    and then convert the sentences into a single story.
    If max_length is supplied,
    any stories longer than max_length tokens will be discarded.
    '''
    data = parse_stories(f.readlines(), only_supporting=only_supporting)
    flatten = lambda data: reduce(lambda x, y: x + y, data)
    data = [(flatten(story), q, answer) for story, q, answer in data if not max_length or len(flatten(story)) < max_length]
    return data


In [5]:
def vectorize_stories(data, word_idx, story_maxlen, query_maxlen):
    X = []
    Xq = []
    Y = []
    for story, query, answer in data:
        x=[word_idx[w] for w in story]
        xq=[word_idx[w] for w in query]
        y=np.zeros(len(word_idx) + 1)
        y[word_idx[answer]]=1
        X.append(x)
        Xq.append(xq)
        Y.append(y)
    return (pad_sequences(X, maxlen=story_maxlen),
            pad_sequences(Xq, maxlen=query_maxlen),
            np.array(Y))


In [6]:
try:
    path = get_file('babi-tasks-v1-2.tar.gz', origin='https://s3.amazonaws.com/text-datasets/babi_tasks_1-20_v1-2.tar.gz')
except:
    print('Error downloading dataset, please download it manually:\n'
          '$ wget http://www.thespermwhale.com/jaseweston/babi/tasks_1-20_v1-2.tar.gz\n'
          '$ mv tasks_1-20_v1-2.tar.gz ~/.keras/datasets/babi-tasks-v1-2.tar.gz')
    raise
tar = tarfile.open(path)


In [7]:
challenges = {'single_supporting_fact_10k': 'tasks_1-20_v1-2/en-10k/qa1_single-supporting-fact_{}.txt'}
challenge_type = 'single_supporting_fact_10k'
challenge = challenges[challenge_type]

print('Extracting stories for the challenge:', challenge_type)
train_stories = get_stories(tar.extractfile(challenge.format('train')))
test_stories = get_stories(tar.extractfile(challenge.format('test')))

Extracting stories for the challenge: single_supporting_fact_10k


/anaconda3/lib/python3.6/re.py:212: FutureWarning: split() requires a non-empty pattern match.
  return _compile(pattern, flags).split(string, maxsplit)


In [8]:
print(train_stories)

[(['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'John', 'went', 'to', 'the', 'hallway', '.'], ['Where', 'is', 'Mary', '?'], 'bathroom'), (['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'John', 'went', 'to', 'the', 'hallway', '.', 'Daniel', 'went', 'back', 'to', 'the', 'hallway', '.', 'Sandra', 'moved', 'to', 'the', 'garden', '.'], ['Where', 'is', 'Daniel', '?'], 'hallway'), (['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'John', 'went', 'to', 'the', 'hallway', '.', 'Daniel', 'went', 'back', 'to', 'the', 'hallway', '.', 'Sandra', 'moved', 'to', 'the', 'garden', '.', 'John', 'moved', 'to', 'the', 'office', '.', 'Sandra', 'journeyed', 'to', 'the', 'bathroom', '.'], ['Where', 'is', 'Daniel', '?'], 'hallway'), (['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'John', 'went', 'to', 'the', 'hallway', '.', 'Daniel', 'went', 'back', 'to', 'the', 'hallway', '.', 'Sandra', 'moved', 'to', 'the', 'garden', '.', 'John', 'moved', 'to', 'the', 'office', '.', 'Sandra', 'journeyed', 'to', 'the', 'bat

In [9]:
print(test_stories)

[(['John', 'travelled', 'to', 'the', 'hallway', '.', 'Mary', 'journeyed', 'to', 'the', 'bathroom', '.'], ['Where', 'is', 'John', '?'], 'hallway'), (['John', 'travelled', 'to', 'the', 'hallway', '.', 'Mary', 'journeyed', 'to', 'the', 'bathroom', '.', 'Daniel', 'went', 'back', 'to', 'the', 'bathroom', '.', 'John', 'moved', 'to', 'the', 'bedroom', '.'], ['Where', 'is', 'Mary', '?'], 'bathroom'), (['John', 'travelled', 'to', 'the', 'hallway', '.', 'Mary', 'journeyed', 'to', 'the', 'bathroom', '.', 'Daniel', 'went', 'back', 'to', 'the', 'bathroom', '.', 'John', 'moved', 'to', 'the', 'bedroom', '.', 'John', 'went', 'to', 'the', 'hallway', '.', 'Sandra', 'journeyed', 'to', 'the', 'kitchen', '.'], ['Where', 'is', 'Sandra', '?'], 'kitchen'), (['John', 'travelled', 'to', 'the', 'hallway', '.', 'Mary', 'journeyed', 'to', 'the', 'bathroom', '.', 'Daniel', 'went', 'back', 'to', 'the', 'bathroom', '.', 'John', 'moved', 'to', 'the', 'bedroom', '.', 'John', 'went', 'to', 'the', 'hallway', '.', 'Sandra

In [10]:
vocab = set()
for story, q, answer in train_stories + test_stories:
    print(story)
    vocab |= set(story + q + [answer])
vocab = sorted(vocab)

# Reserve 0 for masking via pad_sequences
vocab_size = len(vocab) + 1
story_maxlen = max(map(len, (x for x, _, _ in train_stories + test_stories)))
query_maxlen = max(map(len, (x for _, x, _ in train_stories + test_stories)))

['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'John', 'went', 'to', 'the', 'hallway', '.']
['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'John', 'went', 'to', 'the', 'hallway', '.', 'Daniel', 'went', 'back', 'to', 'the', 'hallway', '.', 'Sandra', 'moved', 'to', 'the', 'garden', '.']
['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'John', 'went', 'to', 'the', 'hallway', '.', 'Daniel', 'went', 'back', 'to', 'the', 'hallway', '.', 'Sandra', 'moved', 'to', 'the', 'garden', '.', 'John', 'moved', 'to', 'the', 'office', '.', 'Sandra', 'journeyed', 'to', 'the', 'bathroom', '.']
['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'John', 'went', 'to', 'the', 'hallway', '.', 'Daniel', 'went', 'back', 'to', 'the', 'hallway', '.', 'Sandra', 'moved', 'to', 'the', 'garden', '.', 'John', 'moved', 'to', 'the', 'office', '.', 'Sandra', 'journeyed', 'to', 'the', 'bathroom', '.', 'Mary', 'moved', 'to', 'the', 'hallway', '.', 'Daniel', 'travelled', 'to', 'the', 'office', '.']
['Mary', 'moved', 'to', 'the'

['Sandra', 'moved', 'to', 'the', 'hallway', '.', 'John', 'moved', 'to', 'the', 'hallway', '.', 'Sandra', 'went', 'back', 'to', 'the', 'bedroom', '.', 'Mary', 'travelled', 'to', 'the', 'hallway', '.', 'Mary', 'moved', 'to', 'the', 'garden', '.', 'Mary', 'moved', 'to', 'the', 'office', '.', 'Sandra', 'journeyed', 'to', 'the', 'garden', '.', 'John', 'travelled', 'to', 'the', 'office', '.']
['Sandra', 'moved', 'to', 'the', 'hallway', '.', 'John', 'moved', 'to', 'the', 'hallway', '.', 'Sandra', 'went', 'back', 'to', 'the', 'bedroom', '.', 'Mary', 'travelled', 'to', 'the', 'hallway', '.', 'Mary', 'moved', 'to', 'the', 'garden', '.', 'Mary', 'moved', 'to', 'the', 'office', '.', 'Sandra', 'journeyed', 'to', 'the', 'garden', '.', 'John', 'travelled', 'to', 'the', 'office', '.', 'John', 'went', 'to', 'the', 'hallway', '.', 'Mary', 'travelled', 'to', 'the', 'bedroom', '.']
['Mary', 'journeyed', 'to', 'the', 'garden', '.', 'Daniel', 'went', 'to', 'the', 'kitchen', '.']
['Mary', 'journeyed', 'to', 

['John', 'travelled', 'to', 'the', 'office', '.', 'John', 'moved', 'to', 'the', 'garden', '.', 'John', 'journeyed', 'to', 'the', 'hallway', '.', 'John', 'went', 'to', 'the', 'bathroom', '.', 'Mary', 'moved', 'to', 'the', 'bathroom', '.', 'John', 'went', 'back', 'to', 'the', 'office', '.']
['John', 'travelled', 'to', 'the', 'office', '.', 'John', 'moved', 'to', 'the', 'garden', '.', 'John', 'journeyed', 'to', 'the', 'hallway', '.', 'John', 'went', 'to', 'the', 'bathroom', '.', 'Mary', 'moved', 'to', 'the', 'bathroom', '.', 'John', 'went', 'back', 'to', 'the', 'office', '.', 'Mary', 'went', 'to', 'the', 'bedroom', '.', 'Mary', 'went', 'to', 'the', 'bathroom', '.']
['John', 'travelled', 'to', 'the', 'office', '.', 'John', 'moved', 'to', 'the', 'garden', '.', 'John', 'journeyed', 'to', 'the', 'hallway', '.', 'John', 'went', 'to', 'the', 'bathroom', '.', 'Mary', 'moved', 'to', 'the', 'bathroom', '.', 'John', 'went', 'back', 'to', 'the', 'office', '.', 'Mary', 'went', 'to', 'the', 'bedroom',

['Daniel', 'went', 'to', 'the', 'bathroom', '.', 'John', 'travelled', 'to', 'the', 'bathroom', '.', 'Sandra', 'went', 'to', 'the', 'bathroom', '.', 'Mary', 'travelled', 'to', 'the', 'bathroom', '.', 'John', 'went', 'back', 'to', 'the', 'kitchen', '.', 'Daniel', 'moved', 'to', 'the', 'garden', '.']
['Daniel', 'went', 'to', 'the', 'bathroom', '.', 'John', 'travelled', 'to', 'the', 'bathroom', '.', 'Sandra', 'went', 'to', 'the', 'bathroom', '.', 'Mary', 'travelled', 'to', 'the', 'bathroom', '.', 'John', 'went', 'back', 'to', 'the', 'kitchen', '.', 'Daniel', 'moved', 'to', 'the', 'garden', '.', 'Mary', 'journeyed', 'to', 'the', 'bedroom', '.', 'Sandra', 'went', 'to', 'the', 'hallway', '.']
['Daniel', 'went', 'to', 'the', 'bathroom', '.', 'John', 'travelled', 'to', 'the', 'bathroom', '.', 'Sandra', 'went', 'to', 'the', 'bathroom', '.', 'Mary', 'travelled', 'to', 'the', 'bathroom', '.', 'John', 'went', 'back', 'to', 'the', 'kitchen', '.', 'Daniel', 'moved', 'to', 'the', 'garden', '.', 'Mary'

['Sandra', 'journeyed', 'to', 'the', 'bedroom', '.', 'Daniel', 'went', 'to', 'the', 'office', '.', 'Daniel', 'went', 'back', 'to', 'the', 'bathroom', '.', 'Mary', 'went', 'to', 'the', 'kitchen', '.']
['Sandra', 'journeyed', 'to', 'the', 'bedroom', '.', 'Daniel', 'went', 'to', 'the', 'office', '.', 'Daniel', 'went', 'back', 'to', 'the', 'bathroom', '.', 'Mary', 'went', 'to', 'the', 'kitchen', '.', 'Daniel', 'moved', 'to', 'the', 'garden', '.', 'Daniel', 'went', 'back', 'to', 'the', 'bedroom', '.']
['Sandra', 'journeyed', 'to', 'the', 'bedroom', '.', 'Daniel', 'went', 'to', 'the', 'office', '.', 'Daniel', 'went', 'back', 'to', 'the', 'bathroom', '.', 'Mary', 'went', 'to', 'the', 'kitchen', '.', 'Daniel', 'moved', 'to', 'the', 'garden', '.', 'Daniel', 'went', 'back', 'to', 'the', 'bedroom', '.', 'John', 'moved', 'to', 'the', 'bathroom', '.', 'Mary', 'moved', 'to', 'the', 'office', '.']
['Sandra', 'journeyed', 'to', 'the', 'bedroom', '.', 'Daniel', 'went', 'to', 'the', 'office', '.', 'Dani

...

['Mary', 'went', 'to', 'the', 'bathroom', '.', 'Sandra', 'moved', 'to', 'the', 'kitchen', '.']
['Mary', 'went', 'to', 'the', 'bathroom', '.', 'Sandra', 'moved', 'to', 'the', 'kitchen', '.', 'Sandra', 'went', 'back', 'to', 'the', 'office', '.', 'Mary', 'went', 'back', 'to', 'the', 'office', '.']
['Mary', 'went', 'to', 'the', 'bathroom', '.', 'Sandra', 'moved', 'to', 'the', 'kitchen', '.', 'Sandra', 'went', 'back', 'to', 'the', 'office', '.', 'Mary', 'went', 'back', 'to', 'the', 'office', '.', 'Daniel', 'went', 'to', 'the', 'bedroom', '.', 'Mary', 'journeyed', 'to', 'the', 'kitchen', '.']
['Mary', 'went', 'to', 'the', 'bathroom', '.', 'Sandra', 'moved', 'to', 'the', 'kitchen', '.', 'Sandra', 'went', 'back', 'to', 'the', 'office', '.', 'Mary', 'went', 'back', 'to', 'the', 'office', '.', 'Daniel', 'went', 'to', 'the', 'bedroom', '.', 'Mary', 'journeyed', 'to', 'the', 'kitchen', '.', 'Daniel', 'journeyed', 'to', 'the', 'hallway', '.', 'Daniel', 'went', 'back', 'to', 'the', 'kitchen', '.']
[

['Mary', 'moved', 'to', 'the', 'hallway', '.', 'Mary', 'journeyed', 'to', 'the', 'office', '.']
['Mary', 'moved', 'to', 'the', 'hallway', '.', 'Mary', 'journeyed', 'to', 'the', 'office', '.', 'Sandra', 'went', 'to', 'the', 'office', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedroom', '.']
['Mary', 'moved', 'to', 'the', 'hallway', '.', 'Mary', 'journeyed', 'to', 'the', 'office', '.', 'Sandra', 'went', 'to', 'the', 'office', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedroom', '.', 'Daniel', 'went', 'back', 'to', 'the', 'garden', '.', 'Sandra', 'journeyed', 'to', 'the', 'bathroom', '.']
['Mary', 'moved', 'to', 'the', 'hallway', '.', 'Mary', 'journeyed', 'to', 'the', 'office', '.', 'Sandra', 'went', 'to', 'the', 'office', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedroom', '.', 'Daniel', 'went', 'back', 'to', 'the', 'garden', '.', 'Sandra', 'journeyed', 'to', 'the', 'bathroom', '.', 'Daniel', 'moved', 'to', 'the', 'office', '.', 'Mary', 'went', 'to', 'the', 'bedroom', '.']
['Mary', 'moved'

['Daniel', 'journeyed', 'to', 'the', 'bedroom', '.', 'Mary', 'went', 'to', 'the', 'hallway', '.', 'Daniel', 'went', 'to', 'the', 'office', '.', 'John', 'journeyed', 'to', 'the', 'office', '.', 'Daniel', 'moved', 'to', 'the', 'bedroom', '.', 'Sandra', 'went', 'back', 'to', 'the', 'garden', '.', 'Sandra', 'went', 'to', 'the', 'office', '.', 'John', 'journeyed', 'to', 'the', 'hallway', '.', 'Sandra', 'travelled', 'to', 'the', 'hallway', '.', 'Mary', 'travelled', 'to', 'the', 'garden', '.']
['Sandra', 'journeyed', 'to', 'the', 'hallway', '.', 'Sandra', 'went', 'back', 'to', 'the', 'bedroom', '.']
['Sandra', 'journeyed', 'to', 'the', 'hallway', '.', 'Sandra', 'went', 'back', 'to', 'the', 'bedroom', '.', 'Mary', 'went', 'to', 'the', 'kitchen', '.', 'Daniel', 'went', 'back', 'to', 'the', 'office', '.']
['Sandra', 'journeyed', 'to', 'the', 'hallway', '.', 'Sandra', 'went', 'back', 'to', 'the', 'bedroom', '.', 'Mary', 'went', 'to', 'the', 'kitchen', '.', 'Daniel', 'went', 'back', 'to', 'the', '

['Daniel', 'journeyed', 'to', 'the', 'garden', '.', 'Mary', 'journeyed', 'to', 'the', 'kitchen', '.', 'Sandra', 'went', 'back', 'to', 'the', 'kitchen', '.', 'Sandra', 'travelled', 'to', 'the', 'office', '.', 'John', 'moved', 'to', 'the', 'bathroom', '.', 'Mary', 'went', 'back', 'to', 'the', 'bathroom', '.', 'John', 'journeyed', 'to', 'the', 'bedroom', '.', 'Sandra', 'moved', 'to', 'the', 'garden', '.', 'Mary', 'went', 'to', 'the', 'hallway', '.', 'Daniel', 'moved', 'to', 'the', 'office', '.']
['Daniel', 'travelled', 'to', 'the', 'bedroom', '.', 'Daniel', 'moved', 'to', 'the', 'bathroom', '.']
['Daniel', 'travelled', 'to', 'the', 'bedroom', '.', 'Daniel', 'moved', 'to', 'the', 'bathroom', '.', 'Daniel', 'went', 'back', 'to', 'the', 'hallway', '.', 'John', 'went', 'to', 'the', 'bathroom', '.']
['Daniel', 'travelled', 'to', 'the', 'bedroom', '.', 'Daniel', 'moved', 'to', 'the', 'bathroom', '.', 'Daniel', 'went', 'back', 'to', 'the', 'hallway', '.', 'John', 'went', 'to', 'the', 'bathroom',

['Sandra', 'went', 'back', 'to', 'the', 'hallway', '.', 'Mary', 'went', 'back', 'to', 'the', 'kitchen', '.', 'John', 'journeyed', 'to', 'the', 'bathroom', '.', 'Daniel', 'went', 'back', 'to', 'the', 'hallway', '.', 'Sandra', 'moved', 'to', 'the', 'office', '.', 'Sandra', 'journeyed', 'to', 'the', 'bathroom', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedroom', '.', 'John', 'went', 'to', 'the', 'hallway', '.']
['Sandra', 'went', 'back', 'to', 'the', 'hallway', '.', 'Mary', 'went', 'back', 'to', 'the', 'kitchen', '.', 'John', 'journeyed', 'to', 'the', 'bathroom', '.', 'Daniel', 'went', 'back', 'to', 'the', 'hallway', '.', 'Sandra', 'moved', 'to', 'the', 'office', '.', 'Sandra', 'journeyed', 'to', 'the', 'bathroom', '.', 'Sandra', 'journeyed', 'to', 'the', 'bedroom', '.', 'John', 'went', 'to', 'the', 'hallway', '.', 'Mary', 'went', 'to', 'the', 'bathroom', '.', 'Mary', 'travelled', 'to', 'the', 'bedroom', '.']
['John', 'travelled', 'to', 'the', 'kitchen', '.', 'Sandra', 'moved', 'to', 'the

In [11]:
with open('story_maxlen_single_fact.txt','w') as file:
    file.write(str(story_maxlen))
    file.write('\n')
file.close()


with open('query_maxlen_single_fact.txt','w') as file:
    file.write(str(query_maxlen))
    file.write('\n')
file.close()


In [12]:
print('-')
print('Vocab size:', vocab_size, 'unique words')
print('Story max length:', story_maxlen, 'words')
print('Query max length:', query_maxlen, 'words')
print('Number of training stories:', len(train_stories))
print('Number of test stories:', len(test_stories))
print('-')
print('Here\'s what a "story" tuple looks like (input, query, answer):')
print(train_stories[0])
print('-')
print('Vectorizing the word sequences...')

word_idx = dict((c, i + 1) for i, c in enumerate(vocab))
idx_word = dict((i+1, c) for i,c in enumerate(vocab))
inputs_train, queries_train, answers_train = vectorize_stories(train_stories,
                                                               word_idx,
                                                               story_maxlen,
                                                               query_maxlen)
inputs_test, queries_test, answers_test = vectorize_stories(test_stories,
                                                            word_idx,
                                                            story_maxlen,
                                                            query_maxlen)

-
Vocab size: 22 unique words
Story max length: 68 words
Query max length: 4 words
Number of training stories: 10000
Number of test stories: 1000
-
Here's what a "story" tuple looks like (input, query, answer):
(['Mary', 'moved', 'to', 'the', 'bathroom', '.', 'John', 'went', 'to', 'the', 'hallway', '.'], ['Where', 'is', 'Mary', '?'], 'bathroom')
-
Vectorizing the word sequences...


In [14]:
with open('word_idx_single_fact.txt','w') as file:
    file.write(str(word_idx))
file.close()

In [13]:
with open('idx_word_single_fact.txt','w') as file:
    file.write(str(idx_word))
file.close()

In [15]:
print(word_idx)

{'.': 1, '?': 2, 'Daniel': 3, 'John': 4, 'Mary': 5, 'Sandra': 6, 'Where': 7, 'back': 8, 'bathroom': 9, 'bedroom': 10, 'garden': 11, 'hallway': 12, 'is': 13, 'journeyed': 14, 'kitchen': 15, 'moved': 16, 'office': 17, 'the': 18, 'to': 19, 'travelled': 20, 'went': 21}


In [16]:
print(idx_word)

{1: '.', 2: '?', 3: 'Daniel', 4: 'John', 5: 'Mary', 6: 'Sandra', 7: 'Where', 8: 'back', 9: 'bathroom', 10: 'bedroom', 11: 'garden', 12: 'hallway', 13: 'is', 14: 'journeyed', 15: 'kitchen', 16: 'moved', 17: 'office', 18: 'the', 19: 'to', 20: 'travelled', 21: 'went'}


In [17]:
print('-')
print('inputs: integer tensor of shape (samples, max_length)')
print('inputs_train shape:', inputs_train.shape)
print('inputs_test shape:', inputs_test.shape)
print('-')
print('queries: integer tensor of shape (samples, max_length)')
print('queries_train shape:', queries_train.shape)
print('queries_test shape:', queries_test.shape)
print('-')
print('answers: binary (1 or 0) tensor of shape (samples, vocab_size)')
print('answers_train shape:', answers_train.shape)
print('answers_test shape:', answers_test.shape)
print('-')
print('Compiling...')

-
inputs: integer tensor of shape (samples, max_length)
inputs_train shape: (10000, 68)
inputs_test shape: (1000, 68)
-
queries: integer tensor of shape (samples, max_length)
queries_train shape: (10000, 4)
queries_test shape: (1000, 4)
-
answers: binary (1 or 0) tensor of shape (samples, vocab_size)
answers_train shape: (10000, 22)
answers_test shape: (1000, 22)
-
Compiling...


In [18]:
train_epochs = 120
batch_size = 32
lstm_size = 64

In [19]:
# placeholders
input_sequence = Input((story_maxlen,))
question = Input((query_maxlen,))

print('Input sequence:', input_sequence)
print('Question:', question)

# encoders
# embed the input sequence into a sequence of vectors
input_encoder_m = Sequential()
input_encoder_m.add(Embedding(input_dim=vocab_size,
                              output_dim=64))
input_encoder_m.add(Dropout(0.3))
# output: (samples, story_maxlen, embedding_dim)

# embed the input into a sequence of vectors of size query_maxlen
input_encoder_c = Sequential()
input_encoder_c.add(Embedding(input_dim=vocab_size,
                              output_dim=query_maxlen))
input_encoder_c.add(Dropout(0.3))
# output: (samples, story_maxlen, query_maxlen)

# embed the question into a sequence of vectors
question_encoder = Sequential()
question_encoder.add(Embedding(input_dim=vocab_size,
                               output_dim=64,
                               input_length=query_maxlen))
question_encoder.add(Dropout(0.3))
# output: (samples, query_maxlen, embedding_dim)

# encode input sequence and questions (which are indices)
# to sequences of dense vectors
input_encoded_m = input_encoder_m(input_sequence)
print('Input encoded m', input_encoded_m)
input_encoded_c = input_encoder_c(input_sequence)
print('Input encoded c', input_encoded_c)
question_encoded = question_encoder(question)
print('Question encoded', question_encoded)


# compute a 'match' between the first input vector sequence
# and the question vector sequence
# shape: `(samples, story_maxlen, query_maxlen)
match = merge([input_encoded_m, question_encoded], mode='dot', dot_axes=(2, 2))
print(match.shape)
match = Activation('softmax')(match)
print('Match shape', match)

# add the match matrix with the second input vector sequence
response = merge([match, input_encoded_c], mode='sum')  # (samples, story_maxlen, query_maxlen)
response = Permute((2, 1))(response)  # (samples, query_maxlen, story_maxlen)
print('Response shape', response)

# concatenate the response vector with the question vector sequence
answer = merge([response, question_encoded], mode='concat')
print('Answer shape', answer)

#answer = LSTM(lstm_size, return_sequences=True)(answer)  # Generate tensors of shape 32
#answer = Dropout(0.3)(answer)
answer = LSTM(64)(answer)  # Generate tensors of shape 32
answer = Dropout(0.3)(answer)
answer = Dense(vocab_size)(answer)  # (samples, vocab_size)
# we output a probability distribution over the vocabulary
answer = Activation('softmax')(answer)

Input sequence: Tensor("input_1:0", shape=(?, 68), dtype=float32)
Question: Tensor("input_2:0", shape=(?, 4), dtype=float32)
Input encoded m Tensor("sequential_1/dropout_1/cond/Merge:0", shape=(?, 68, 64), dtype=float32)
Input encoded c Tensor("sequential_2/dropout_2/cond/Merge:0", shape=(?, 68, 4), dtype=float32)
Question encoded Tensor("sequential_3/dropout_3/cond/Merge:0", shape=(?, 4, 64), dtype=float32)
(?, 68, 4)
Match shape Tensor("activation_1/truediv:0", shape=(?, 68, 4), dtype=float32)
Response shape Tensor("permute_1/transpose:0", shape=(?, 4, 68), dtype=float32)
Answer shape Tensor("merge_3/concat:0", shape=(?, 4, 132), dtype=float32)


/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:44: UserWarning: The `merge` function is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
/anaconda3/lib/python3.6/site-packages/keras/legacy/layers.py:465: UserWarning: The `Merge` layer is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
  name=name)
/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:50: UserWarning: The `merge` function is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:55: UserWarning: The `merge` function is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.


In [20]:
model = Model([input_sequence, question], answer)
model.compile(optimizer='rmsprop', loss='categorical_crossentropy',
              metrics=['accuracy'])

In [21]:
model.fit([inputs_train, queries_train], answers_train, batch_size, train_epochs,
          validation_data=([inputs_test, queries_test], answers_test))

Train on 10000 samples, validate on 1000 samples
Epoch 1/120
10000/10000 [==============================] - 6s 571us/step - loss: 1.8714 - acc: 0.1760 - val_loss: 1.7734 - val_acc: 0.2280
Epoch 2/120
10000/10000 [==============================] - 6s 556us/step - loss: 1.6855 - acc: 0.2734 - val_loss: 1.6245 - val_acc: 0.3330
Epoch 3/120
10000/10000 [==============================] - 6s 550us/step - loss: 1.5614 - acc: 0.3861 - val_loss: 1.4983 - val_acc: 0.4250
Epoch 4/120
10000/10000 [==============================] - 6s 557us/step - loss: 1.4928 - acc: 0.4224 - val_loss: 1.4539 - val_acc: 0.4320
Epoch 5/120
10000/10000 [==============================] - 6s 573us/step - loss: 1.4473 - acc: 0.4476 - val_loss: 1.3831 - val_acc: 0.4820
Epoch 6/120
10000/10000 [==============================] - 6s 570us/step - loss: 1.3871 - acc: 0.4662 - val_loss: 1.3413 - val_acc: 0.4840
Epoch 7/120
10000/10000 [==============================] - 5s 534us/step - loss: 1.3508 - acc: 0.4792 - val_loss: 1.2

10000/10000 [==============================] - 5s 521us/step - loss: 0.1354 - acc: 0.9518 - val_loss: 0.2699 - val_acc: 0.9120
Epoch 60/120
10000/10000 [==============================] - 5s 516us/step - loss: 0.1230 - acc: 0.9563 - val_loss: 0.2590 - val_acc: 0.9090
Epoch 61/120
10000/10000 [==============================] - 5s 518us/step - loss: 0.1213 - acc: 0.9593 - val_loss: 0.2691 - val_acc: 0.9100
Epoch 62/120
10000/10000 [==============================] - 5s 514us/step - loss: 0.1087 - acc: 0.9625 - val_loss: 0.2319 - val_acc: 0.9290
Epoch 63/120
10000/10000 [==============================] - 5s 518us/step - loss: 0.1009 - acc: 0.9639 - val_loss: 0.2281 - val_acc: 0.9300
Epoch 64/120
10000/10000 [==============================] - 5s 517us/step - loss: 0.1030 - acc: 0.9635 - val_loss: 0.2202 - val_acc: 0.9320
Epoch 65/120
10000/10000 [==============================] - 5s 541us/step - loss: 0.0971 - acc: 0.9685 - val_loss: 0.2242 - val_acc: 0.9310
Epoch 66/120
10000/10000 [=======

10000/10000 [==============================] - 5s 522us/step - loss: 0.0248 - acc: 0.9928 - val_loss: 0.3028 - val_acc: 0.9440
Epoch 118/120
10000/10000 [==============================] - 5s 524us/step - loss: 0.0167 - acc: 0.9946 - val_loss: 0.2993 - val_acc: 0.9420
Epoch 119/120
10000/10000 [==============================] - 5s 523us/step - loss: 0.0192 - acc: 0.9947 - val_loss: 0.2558 - val_acc: 0.9550
Epoch 120/120
10000/10000 [==============================] - 5s 530us/step - loss: 0.0182 - acc: 0.9947 - val_loss: 0.2723 - val_acc: 0.9500


In [22]:
for i in range(0,10):
        current_inp = test_stories[i]
        current_story, current_query, current_answer = vectorize_stories([current_inp], word_idx, story_maxlen, query_maxlen)
        current_prediction = model.predict([current_story, current_query])
        current_prediction = idx_word[np.argmax(current_prediction)]
        print(' '.join(current_inp[0]), ' '.join(current_inp[1]), '| Prediction:', current_prediction, '| Ground Truth:', current_inp[2])
        print("-----------------------------------------------------------------------------------------")
        

John travelled to the hallway . Mary journeyed to the bathroom . Where is John ? | Prediction: hallway | Ground Truth: hallway
-----------------------------------------------------------------------------------------
John travelled to the hallway . Mary journeyed to the bathroom . Daniel went back to the bathroom . John moved to the bedroom . Where is Mary ? | Prediction: bathroom | Ground Truth: bathroom
-----------------------------------------------------------------------------------------
John travelled to the hallway . Mary journeyed to the bathroom . Daniel went back to the bathroom . John moved to the bedroom . John went to the hallway . Sandra journeyed to the kitchen . Where is Sandra ? | Prediction: kitchen | Ground Truth: kitchen
-----------------------------------------------------------------------------------------
John travelled to the hallway . Mary journeyed to the bathroom . Daniel went back to the bathroom . John moved to the bedroom . John went to the hallway . San

In [23]:
print(story)

['Sandra', 'moved', 'to', 'the', 'kitchen', '.', 'John', 'travelled', 'to', 'the', 'kitchen', '.', 'Sandra', 'moved', 'to', 'the', 'hallway', '.', 'Daniel', 'journeyed', 'to', 'the', 'hallway', '.', 'Sandra', 'travelled', 'to', 'the', 'office', '.', 'John', 'moved', 'to', 'the', 'bedroom', '.', 'Sandra', 'went', 'back', 'to', 'the', 'garden', '.', 'Sandra', 'travelled', 'to', 'the', 'bathroom', '.', 'Sandra', 'moved', 'to', 'the', 'office', '.', 'Daniel', 'journeyed', 'to', 'the', 'garden', '.']


In [24]:
from keras.models import model_from_json
model_json = model.to_json()
with open("model_single_fact.json", "w") as json_file:
    json_file.write(model_json)
# serialize weights to HDF5
model.save_weights("model_single_fact.h5")
print("Saved model to disk")

Saved model to disk


In [25]:
json_file = open('model_single_fact.json', 'r')
loaded_model_json = json_file.read()
json_file.close()
loaded_model = model_from_json(loaded_model_json)
# load weights into new model
loaded_model.load_weights("model_single_fact.h5")

/anaconda3/lib/python3.6/site-packages/keras/engine/topology.py:1271: UserWarning: The `Merge` layer is deprecated and will be removed after 08/2017. Use instead layers from `keras.layers.merge`, e.g. `add`, `concatenate`, etc.
  return cls(**config)


In [26]:
test_stories[0]

(['John',
  'travelled',
  'to',
  'the',
  'hallway',
  '.',
  'Mary',
  'journeyed',
  'to',
  'the',
  'bathroom',
  '.'],
 ['Where', 'is', 'John', '?'],
 'hallway')

In [27]:
loaded_model.compile(optimizer='rmsprop', loss='categorical_crossentropy',
              metrics=['accuracy'])
for i in range(0,10):
        current_inp = test_stories[i]
        current_story, current_query, current_answer = vectorize_stories([current_inp], word_idx, story_maxlen, query_maxlen)
        current_prediction = loaded_model.predict([current_story, current_query])
        current_prediction = idx_word[np.argmax(current_prediction)]
        print(' '.join(current_inp[0]), ' '.join(current_inp[1]), '| Prediction:', current_prediction, '| Ground Truth:', current_inp[2])
        print("-----------------------------------------------------------------------------------------")


John travelled to the hallway . Mary journeyed to the bathroom . Where is John ? | Prediction: hallway | Ground Truth: hallway
-----------------------------------------------------------------------------------------
John travelled to the hallway . Mary journeyed to the bathroom . Daniel went back to the bathroom . John moved to the bedroom . Where is Mary ? | Prediction: bathroom | Ground Truth: bathroom
-----------------------------------------------------------------------------------------
John travelled to the hallway . Mary journeyed to the bathroom . Daniel went back to the bathroom . John moved to the bedroom . John went to the hallway . Sandra journeyed to the kitchen . Where is Sandra ? | Prediction: kitchen | Ground Truth: kitchen
-----------------------------------------------------------------------------------------
John travelled to the hallway . Mary journeyed to the bathroom . Daniel went back to the bathroom . John moved to the bedroom . John went to the hallway . San

In [28]:
print(current_story)

[[ 0  0  0  0  0  0  0  0  6 20 19 18 15  1  6 20 19 18 12  1  5 21 19 18
   9  1  6 16 19 18 11  1  6 20 19 18 17  1  3 14 19 18 12  1  3 14 19 18
  17  1  4 16 19 18 12  1  4 20 19 18  9  1  4 14 19 18 17  1]]


In [29]:
print(current_query)

[[ 7 13  3  2]]


In [30]:
print(len(current_query))

1


In [31]:
print(test_stories[0])

(['John', 'travelled', 'to', 'the', 'hallway', '.', 'Mary', 'journeyed', 'to', 'the', 'bathroom', '.'], ['Where', 'is', 'John', '?'], 'hallway')
